# Erode and dilate masks
Notebook author: Thorbjørn Erik Køppen Christensen (tekc@dtu.dk)

This notebook can be used to run erosion and dilation on binary masks.
This can be useful for removing "noisy" attatchments, closing holes and smoothing edges of masks.
Can run in either 2D (circle) or 3D (sphere). Note that the 3D version is somewhat more expensive in memory requirements

## Import Libraries

In [31]:
import numpy as np
import h5py
import qim3d
import scipy.ndimage

## Define functions

In [77]:
def structure_sphere(r,dims=3):
    #Creates a sphere of with radius r in dims dimensions
    #r is in pixels
    
    d = 2*r-1 #The "-1" is to combat a small offeset from indexing starting at 0
    #Define the center for dims dimensions
    if r % 2 ==0:
        center = (np.s_[r-1:r],)*dims 
    else:
        center = np.s_[(r-1,)*dims]
        
    #turn everything within r indices of center into 1
    vol = np.zeros((d,)*dims)
    vol[center] = 1
    distance = scipy.ndimage.distance_transform_edt(1-vol)
    vol[distance<=r-1] = 1
    vol[distance>1] = 0
    return vol

## Load data

In [71]:
# Load data
filename = "../resources/img3d/shell_225x128x128_bin_mask.h5"
vol = qim3d.io.load(filename) 

## Erode and dilate

In [80]:
# Erode and dilate

vol = structure_sphere(100)
sphere = structure_sphere(5)
vol = scipy.ndimage.binary_erosion(vol, structure=sphere.astype(vol.dtype))
vol = scipy.ndimage.binary_dilation(vol, structure=sphere.astype(vol.dtype))

## Save eroded/dilated volume

In [81]:
#Save binary_segmentation
save_folder = '../resources/img3d/'
save_file = filename.split('/')[-1].split('.')[0] + '_eroded_dilated.h5'
with h5py.file(os.path.join(save_folder,save_file),'w') as sfile:
    sfile.create_dataset('mask/eroded',data=vol)

(slice(1, 2, None), slice(1, 2, None), slice(1, 2, None))